Import Library

In [1]:
import os
import tensorflow as tf
from tfx.orchestration.experimental.interactive.interactive_context import InteractiveContext
from tfx.components import CsvExampleGen, StatisticsGen, SchemaGen, ExampleValidator, Tuner, Transform, Trainer, Evaluator, Pusher
from tfx.proto import example_gen_pb2, trainer_pb2, pusher_pb2
import tensorflow_model_analysis as tfma
from tfx.dsl.components.common.resolver import Resolver
from tfx.dsl.input_resolution.strategies.latest_blessed_model_strategy import LatestBlessedModelStrategy

2025-08-14 16:21:45.332706: I external/local_tsl/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.
2025-08-14 16:21:45.361011: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-08-14 16:21:45.361057: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-08-14 16:21:45.362194: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-08-14 16:21:45.367883: I external/local_tsl/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.
2025-08-14 16:21:45.368660: I tensorflow/core/platform/cpu_feature_guard.cc:1

Inisialisasi dan Setup Path

In [2]:
# Lokasi dan nama-nama file/folder
PIPELINE_NAME = "rifkyadi-pipeline"
SCHEMA_PIPELINE_NAME = "mobile-price-schema"

# Direktori untuk menyimpan output pipeline
PIPELINE_ROOT = os.path.join(PIPELINE_NAME)
# Direktori untuk menyimpan metadata
METADATA_PATH = os.path.join('metadata', PIPELINE_NAME, 'metadata.db')
# Direktori untuk menyimpan model yang siap di-deploy
SERVING_MODEL_DIR = os.path.join('../serving_model')

#Path ke file modul
TRANSFORM_MODULE_FILE = "modules/transform.py"
TRAINER_MODULE_FILE = "modules/trainer.py"

# Path ke dataset
DATA_ROOT = os.path.abspath('../dataset')

# Inisialisasi InteractiveContext
context = InteractiveContext(pipeline_root=PIPELINE_ROOT)

ExampleGen: Mengambil Data

In [3]:
# Konfigurasi input untuk membagi data dari folder DATA_ROOT
input_config = example_gen_pb2.Input(splits=[
    example_gen_pb2.Input.Split(name='train', pattern='train.csv*')
])

output_config = example_gen_pb2.Output(
    split_config=example_gen_pb2.SplitConfig(splits=[
        example_gen_pb2.SplitConfig.Split(name='train', hash_buckets=8),
        example_gen_pb2.SplitConfig.Split(name='eval', hash_buckets=2)
    ])
)

# Buat instance ExampleGen
example_gen = CsvExampleGen(input_base=DATA_ROOT, input_config=input_config, output_config=output_config)
# Jalankan komponen
context.run(example_gen)

ExecutionResult(
    component_id: CsvExampleGen
    execution_id: 3
    outputs:
        examples: OutputChannel(artifact_type=Examples, producer_component_id=CsvExampleGen, output_key=examples, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

StatisticsGen & SchemaGen: Menganalisis dan Membuat Skema Data

In [4]:
# Menghitung statistik dari output ExampleGen
statistics_gen = StatisticsGen(
    examples=example_gen.outputs['examples']
)
context.run(statistics_gen)

# Membuat skema dari output StatisticsGen
schema_gen = SchemaGen(
    statistics=statistics_gen.outputs['statistics']
)
context.run(schema_gen)

ExecutionResult(
    component_id: SchemaGen
    execution_id: 5
    outputs:
        schema: OutputChannel(artifact_type=Schema, producer_component_id=SchemaGen, output_key=schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

ExampleValidator: Memvalidasi Data

In [5]:
example_validator = ExampleValidator(
    statistics=statistics_gen.outputs['statistics'],
    schema=schema_gen.outputs['schema']
)
context.run(example_validator)

ExecutionResult(
    component_id: ExampleValidator
    execution_id: 6
    outputs:
        anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=ExampleValidator, output_key=anomalies, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

Transform: Preprocessing Data

In [6]:
transform = Transform(
    examples=example_gen.outputs['examples'],
    schema=schema_gen.outputs['schema'],
    module_file=os.path.abspath(TRANSFORM_MODULE_FILE)
)
context.run(transform)

running bdist_wheel
running build
running build_py
creating build/lib
copying trainer.py -> build/lib
copying transform.py -> build/lib
installing to /tmp/tmpr5jyzdyp
running install
running install_lib
copying build/lib/transform.py -> /tmp/tmpr5jyzdyp/.
copying build/lib/trainer.py -> /tmp/tmpr5jyzdyp/.
running install_egg_info
running egg_info
creating tfx_user_code_Transform.egg-info
writing tfx_user_code_Transform.egg-info/PKG-INFO
writing dependency_links to tfx_user_code_Transform.egg-info/dependency_links.txt
writing top-level names to tfx_user_code_Transform.egg-info/top_level.txt
writing manifest file 'tfx_user_code_Transform.egg-info/SOURCES.txt'
reading manifest file 'tfx_user_code_Transform.egg-info/SOURCES.txt'
writing manifest file 'tfx_user_code_Transform.egg-info/SOURCES.txt'
Copying tfx_user_code_Transform.egg-info to /tmp/tmpr5jyzdyp/./tfx_user_code_Transform-0.0+9428a1ce7404fea54f275e5790a12b74670f5e2a3ea36ff33b79733cc7f84f78-py3.10.egg-info
running install_scripts


/home/arch/.anaconda3/envs/mlops/lib/python3.10/site-packages/setuptools/_distutils/cmd.py:90: SetuptoolsDeprecationWarning: setup.py install is deprecated.
!!

        ********************************************************************************
        Please avoid running ``setup.py`` directly.
        Instead, use pypa/build, pypa/installer or other
        standards-based tools.

        By 2025-Oct-31, you need to update your project and remove deprecated calls
        or your builds will no longer be supported.

        See https://blog.ganssle.io/articles/2021/10/setup-py-deprecated.html for details.
        ********************************************************************************

!!
  self.initialize_options()


Processing ./rifkyadi-pipeline/_wheels/tfx_user_code_transform-0.0+9428a1ce7404fea54f275e5790a12b74670f5e2a3ea36ff33b79733cc7f84f78-py3-none-any.whl
Processing ./rifkyadi-pipeline/_wheels/tfx_user_code_transform-0.0+9428a1ce7404fea54f275e5790a12b74670f5e2a3ea36ff33b79733cc7f84f78-py3-none-any.whl
Processing ./rifkyadi-pipeline/_wheels/tfx_user_code_transform-0.0+9428a1ce7404fea54f275e5790a12b74670f5e2a3ea36ff33b79733cc7f84f78-py3-none-any.whl
INFO:tensorflow:Assets written to: rifkyadi-pipeline/Transform/transform_graph/7/.temp_path/tftransform_tmp/2a2da405ab414e869f703b3d86d9ee10/assets


INFO:tensorflow:Assets written to: rifkyadi-pipeline/Transform/transform_graph/7/.temp_path/tftransform_tmp/2a2da405ab414e869f703b3d86d9ee10/assets


INFO:tensorflow:struct2tensor is not available.


...

INFO:tensorflow:tensorflow_decision_forests is not available.


INFO:tensorflow:tensorflow_decision_forests is not available.


INFO:tensorflow:tensorflow_text is not available.


INFO:tensorflow:tensorflow_text is not available.


ExecutionResult(
    component_id: Transform
    execution_id: 7
    outputs:
        transform_graph: OutputChannel(artifact_type=TransformGraph, producer_component_id=Transform, output_key=transform_graph, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        transformed_examples: OutputChannel(artifact_type=Examples, producer_component_id=Transform, output_key=transformed_examples, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        updated_analyzer_cache: OutputChannel(artifact_type=TransformCache, producer_component_id=Transform, output_key=updated_analyzer_cache, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        pre_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=pre_transform_schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        pre_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=pre_transform_stats, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        post_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=post_transform_schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        post_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=post_transform_stats, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        post_transform_anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=Transform, output_key=post_transform_anomalies, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

Tuner: Mencari hyperparameter terbaik

In [7]:
tuner = Tuner(
    module_file=os.path.abspath(TRAINER_MODULE_FILE), 
    examples=transform.outputs['transformed_examples'],
    transform_graph=transform.outputs['transform_graph'],
    schema=schema_gen.outputs['schema'],
    train_args=trainer_pb2.TrainArgs(num_steps=800),
    eval_args=trainer_pb2.EvalArgs(num_steps=100)
)
context.run(tuner)

Trial 5 Complete [00h 00m 12s]
val_sparse_categorical_accuracy: 0.9050925970077515

Best val_sparse_categorical_accuracy So Far: 0.9515669345855713
Total elapsed time: 00h 01m 07s
Results summary
Results in rifkyadi-pipeline/.temp/8/model_tuning
Showing 10 best trials
Objective(name="val_sparse_categorical_accuracy", direction="max")

Trial 3 summary
Hyperparameters:
units: 352
learning_rate: 0.0001
Score: 0.9515669345855713

Trial 0 summary
Hyperparameters:
units: 416
learning_rate: 0.001
Score: 0.9364316463470459

Trial 1 summary
Hyperparameters:
units: 480
learning_rate: 0.01
Score: 0.9237892031669617

Trial 2 summary
Hyperparameters:
units: 512
learning_rate: 0.01
Score: 0.9106125235557556

Trial 4 summary
Hyperparameters:
units: 416
learning_rate: 0.01
Score: 0.9050925970077515


ExecutionResult(
    component_id: Tuner
    execution_id: 8
    outputs:
        best_hyperparameters: OutputChannel(artifact_type=HyperParameters, producer_component_id=Tuner, output_key=best_hyperparameters, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        tuner_results: OutputChannel(artifact_type=TunerResults, producer_component_id=Tuner, output_key=tuner_results, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

Trainer: Melatih model ML

In [8]:
trainer = Trainer(
    module_file=os.path.abspath(TRAINER_MODULE_FILE),
    examples=transform.outputs['transformed_examples'],
    transform_graph=transform.outputs['transform_graph'],
    schema=schema_gen.outputs['schema'],
    hyperparameters=tuner.outputs['best_hyperparameters'],
    train_args=trainer_pb2.TrainArgs(num_steps=100),
    eval_args=trainer_pb2.EvalArgs(num_steps=50)
)
context.run(trainer)

running bdist_wheel
running build
running build_py
creating build/lib
copying trainer.py -> build/lib
copying transform.py -> build/lib


/home/arch/.anaconda3/envs/mlops/lib/python3.10/site-packages/setuptools/_distutils/cmd.py:90: SetuptoolsDeprecationWarning: setup.py install is deprecated.
!!

        ********************************************************************************
        Please avoid running ``setup.py`` directly.
        Instead, use pypa/build, pypa/installer or other
        standards-based tools.

        By 2025-Oct-31, you need to update your project and remove deprecated calls
        or your builds will no longer be supported.

        See https://blog.ganssle.io/articles/2021/10/setup-py-deprecated.html for details.
        ********************************************************************************

!!
  self.initialize_options()


installing to /tmp/tmppdzynlgz
running install
running install_lib
copying build/lib/transform.py -> /tmp/tmppdzynlgz/.
copying build/lib/trainer.py -> /tmp/tmppdzynlgz/.
running install_egg_info
running egg_info
creating tfx_user_code_Trainer.egg-info
writing tfx_user_code_Trainer.egg-info/PKG-INFO
writing dependency_links to tfx_user_code_Trainer.egg-info/dependency_links.txt
writing top-level names to tfx_user_code_Trainer.egg-info/top_level.txt
writing manifest file 'tfx_user_code_Trainer.egg-info/SOURCES.txt'
reading manifest file 'tfx_user_code_Trainer.egg-info/SOURCES.txt'
writing manifest file 'tfx_user_code_Trainer.egg-info/SOURCES.txt'
Copying tfx_user_code_Trainer.egg-info to /tmp/tmppdzynlgz/./tfx_user_code_Trainer-0.0+9428a1ce7404fea54f275e5790a12b74670f5e2a3ea36ff33b79733cc7f84f78-py3.10.egg-info
running install_scripts
creating /tmp/tmppdzynlgz/tfx_user_code_trainer-0.0+9428a1ce7404fea54f275e5790a12b74670f5e2a3ea36ff33b79733cc7f84f78.dist-info/WHEEL
creating '/tmp/tmpvyj

INFO:tensorflow:struct2tensor is not available.


INFO:tensorflow:tensorflow_decision_forests is not available.


...

INFO:tensorflow:tensorflow_text is not available.


INFO:tensorflow:tensorflow_text is not available.


INFO:tensorflow:Assets written to: rifkyadi-pipeline/Trainer/model/9/Format-Serving/assets


INFO:tensorflow:Assets written to: rifkyadi-pipeline/Trainer/model/9/Format-Serving/assets


ExecutionResult(
    component_id: Trainer
    execution_id: 9
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=Trainer, output_key=model, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        model_run: OutputChannel(artifact_type=ModelRun, producer_component_id=Trainer, output_key=model_run, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

Resolver, Evaluator, dan Pusher: Memilih artefak versi terbaik/terbaru untuk digunakan, Mengevaluasi performa model sebelum deployment, dan Mengirim model yang lolos evaluasi ke deployment.

In [9]:
# Konfigurasi untuk komponen Evaluator.
eval_config = tfma.EvalConfig(
    model_specs=[tfma.ModelSpec(label_key='price_range')],
    slicing_specs=[tfma.SlicingSpec()],
    metrics_specs=[
        tfma.MetricsSpec(metrics=[
            tfma.MetricConfig(class_name='SparseCategoricalAccuracy',
                              threshold=tfma.MetricThreshold(
                                  value_threshold=tfma.GenericValueThreshold(lower_bound={'value': 0.2}),
                                  change_threshold=tfma.GenericChangeThreshold(
                                      direction=tfma.MetricDirection.HIGHER_IS_BETTER,
                                      absolute={'value': -1e-10})
                              )
            )
        ])
    ]
)

# Deklarasikan Evaluator terlebih dahulu untuk membuat channel output 'blessing' yang dibutuhkan oleh Resolver.
evaluator = Evaluator(
    examples=example_gen.outputs['examples'],
    model=trainer.outputs['model'],
    eval_config=eval_config
)

# Deklarasikan Resolver yang menggunakan channel 'model' dari Trainer dan channel 'blessing' dari Evaluator.
model_resolver = Resolver(
    strategy_class=LatestBlessedModelStrategy,
    model=trainer.outputs['model'],
    model_blessing=evaluator.outputs['blessing']
).with_id('latest_blessed_model_resolver')

context.run(model_resolver)

# Hubungkan output dari Resolver sebagai baseline_model untuk Evaluator, lalu jalankan Evaluator.
evaluator.inputs['baseline_model'] = model_resolver.outputs['model']
context.run(evaluator)


# Push model ke direktori serving jika lolos evaluasi dari Evaluator.
pusher = Pusher(
    model=trainer.outputs['model'],
    model_blessing=evaluator.outputs['blessing'],
    push_destination=pusher_pb2.PushDestination(
        filesystem=pusher_pb2.PushDestination.Filesystem(
            base_directory=SERVING_MODEL_DIR
        )
    )
)

context.run(pusher)


Failed at key ['battery_power'] in {'battery_power': array([[1021]]), 'blue': array([[1]]), 'clock_speed': array([[0.5]], dtype=float32), 'dual_sim': array([[1]]), 'fc': array([[0]]), 'four_g': array([[1]]), 'int_memory': array([[53]]), 'm_dep': array([[0.7]], dtype=float32), 'mobile_wt': array([[136]]), 'n_cores': array([[3]]), 'pc': array([[6]]), 'px_height': array([[905]]), 'px_width': array([[1988]]), 'ram': array([[2631]]), 'sc_h': array([[17]]), 'sc_w': array([[3]]), 'talk_time': array([[7]]), 'three_g': array([[1]]), 'touch_screen': array([[1]]), 'wifi': array([[0]])} and specs {'battery_power': TensorSpec(shape=(None, 1), dtype=tf.float32, name='battery_power'), 'blue': TensorSpec(shape=(None, 1), dtype=tf.float32, name='blue'), 'clock_speed': TensorSpec(shape=(None, 1), dtype=tf.float32, name='clock_speed'), 'dual_sim': TensorSpec(shape=(None, 1), dtype=tf.float32, name='dual_sim'), 'fc': TensorSpec(shape=(None, 1), dtype=tf.float32, name='fc'), 'four_g': TensorSpec(shape=(No

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


ExecutionResult(
    component_id: Pusher
    execution_id: 12
    outputs:
        pushed_model: OutputChannel(artifact_type=PushedModel, producer_component_id=Pusher, output_key=pushed_model, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))